# IBM Applied Data Science Capstone – Coursera
Opening a new Coffee shop in New York, USA
New investor is looking to start a new Coffee Shop in New York, USA neighborhoods

.Build a dataframe of neighborhoods of New York, USA by web scraping the data from Wikipedia page
.Get the geographical coordinates of the neighborhoods
.Obtain the venue data for the neighborhoods from Foursquare API
.Explore and cluster the neighborhoods
.Select the best cluster to open a new Coffee Shop


### Introduction
New York City is one of the most famous, romanticized and desired cities for living in the world due to its image portrayed in the pop culture. Some of the worlds' most popular content creators and influencers are located in the city for its stunning backgrounds and instagrammable dining and coffee locations. Combining that with the overall growing trend for coffee and small business coffee shops makes it an attractive investment to open a new coffee shop specifically in NYC where this coffee shop is likely to receive a lot of attention on social media to drive revenue.

Based on the business type and for the sake of this capstone project, our simplified assumptions for the best location would be a high-density population area with a relatively low number of existing coffee shops. Existing competition might in reality be a good factor as a specific neighborhood could be famous for its coffee shops and would attract more customers. In this project, we will examine the landscape of the city on existing competition to identify the best location for the investment.



### Data
Data required to approach the above business case should include New York City neighborhoods' and boroughs' geographical locations (latitude, longitude) and boroughs' population density.

New York City data containing the neighborhoods and boroughs latitudes and longitudes can be obtained from  https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json. While FourSquare API will be used to obtain data on existing coffee shops.



### Methodology
After collecting the data, it will be wrangled into a dataframe format. Using the density data all above average density boroughs will be mapped onto the map. Then using Foursquare we will locate all venues in the following boroughs and then filter by "coffee shop" locations. Finally, the data be will be visually assessed from the resulted map.



### Business Problem
What is the best location(s) for coffee shop in New York City? In what Neighborhood and/or borough is preferred for investing into coffee shop business? What (if any) neighborhood is to go to for a cup of coffee?

###  Import libraries

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
%matplotlib inline
#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library


print('Libraries imported.')

Libraries imported.


###  Scrap data from IBM into a DataFrame

In [3]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
newyork_data['features'][0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [6]:
columns_name=['Borough', 'Neighborhood', 'Latitude', 'Longitude']
neighborhoods = pd.DataFrame(columns=columns_name)
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [7]:
neighborhoods_data=newyork_data['features']
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

#### We had some Duplicates on neighborhoods so we change them and set their names like(Borough+Neighborhood)

In [8]:
# venues_df[venues_df.duplicated['Neighborhood']]
dd=neighborhoods['Neighborhood']
# pp=venues_df.
new=neighborhoods[dd.isin(dd[dd.duplicated()])]
neighborhoods2=neighborhoods[~dd.isin(dd[dd.duplicated()])]

new['Neighborhood']=new['Borough']+"_"+new['Neighborhood']
# neighborhoods.join(new.set_index('Neighborhood'), on=["Borough","Latitude","Longitude"])
neighborhoods=pd.concat([new,neighborhoods2])
neighborhoods=neighborhoods.sort_index()


<ipython-input-8-2e3ee190a87a>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new['Neighborhood']=new['Borough']+"_"+new['Neighborhood']


In [9]:
print("The dataframe has {} boroughs and {} neighborhoods".format( len(neighborhoods['Borough'].unique()),neighborhoods.shape[0]))

The dataframe has 5 boroughs and 306 neighborhoods


In [10]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [11]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [12]:
CLIENT_ID = 'PNSBWFVXYOJKYJPV1JT3MJMILB3PLRLAMYBSBCRMNWNVNZRH' # your Foursquare ID
CLIENT_SECRET = 'JGJHDJR1UALFBCQOZSFBNVLCEW3ZMDCESRRP4W5ACVHLY1NK' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: PNSBWFVXYOJKYJPV1JT3MJMILB3PLRLAMYBSBCRMNWNVNZRH
CLIENT_SECRET:JGJHDJR1UALFBCQOZSFBNVLCEW3ZMDCESRRP4W5ACVHLY1NK


In [13]:
radius = 5000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [120]:
# neighborhood_latitude=40.87655077879964 
# neighborhood_longitude= -73.91065965862981
# venue_id='55f81cd2498ee903149fcc64'
# LIMIT = 100
# radius = 500
# url = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(
#         venue_id,
#         CLIENT_ID, 
#         CLIENT_SECRET, 
#         VERSION)
# requests.get(url).json()["response"]
# lat=40.87655077879964 
# lng= -73.91065965862981
# venue_id='55f81cd2498ee903149fcc64'
# LIMIT = 100
# radius = 500
# url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
#         CLIENT_ID, 
#         CLIENT_SECRET, 
#         VERSION, 
#         lat, 
#         lng, 
#         radius, 
#         LIMIT)
# requests.get(url).json()

{'meta': {'code': 200, 'requestId': '611d61f1f7a6451afa2bc05f'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 23,
  'suggestedBounds': {'ne': {'lat': 40.88105078329964,
    'lng': -73.90471933917806},
   'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4baf59e8f964a520a6f93be3',
       'name': 'Bikram Yoga',
       'location': {'address': '5500 Broadway',
        'crossStreet': '230th Street',
        'lat': 40.876843690797934,
        'lng': -73.90620384419528,
        'labeledLatLngs': [{'la

In [14]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'Venue_Name', 'Venue_Latitude', 'Venue_Longitude', 'Venue_Category']

print(venues_df.shape)
venues_df.head()


(30526, 7)


Neighborhood   Latitude  Longitude                   Venue_Name  \
0    Wakefield  40.894705 -73.847201             Lollipops Gelato   
1    Wakefield  40.894705 -73.847201              Ali's Roti Shop   
2    Wakefield  40.894705 -73.847201           Ripe Kitchen & Bar   
3    Wakefield  40.894705 -73.847201     Kingston Tropical Bakery   
4    Wakefield  40.894705 -73.847201  Jackie's West Indian Bakery   

   Venue_Latitude  Venue_Longitude        Venue_Category  
0       40.894123       -73.845892          Dessert Shop  
1       40.894036       -73.856935  Caribbean Restaurant  
2       40.898152       -73.838875  Caribbean Restaurant  
3       40.888568       -73.859885                Bakery  
4       40.889283       -73.843310  Caribbean Restaurant

In [15]:
bb=venues_df[venues_df['Venue_Category']=='Coffee Shop']
cc=bb.groupby(['Neighborhood']).count()
copy=cc.sort_values(ascending=False,by='Venue_Category')
copy

Latitude  Longitude  Venue_Name  Venue_Latitude  \
Neighborhood                                                                 
Prospect Lefferts Gardens         6          6           6               6   
Prince's Bay                      6          6           6               6   
Hamilton Heights                  6          6           6               6   
Bushwick                          6          6           6               6   
Gowanus                           6          6           6               6   
Melrose                           6          6           6               6   
New Lots                          6          6           6               6   
Clason Point                      6          6           6               6   
Red Hook                          6          6           6               6   
Ocean Hill                        6          6           6               6   
Old Town                          6          6           6               6   
Concourse Village                 6          6           6               6   
Country Club                      6          6           6               6   
Castle Hill                       5          5           5               5   
Cypress Hills                     5          5           5               5   
Park Slope                        5          5           5               5   
Downtown                          5          5           5               5   
East New York                     5          5           5               5   
Pelham Bay                        5          5           5               5   
Boerum Hill                       5          5           5               5   
Erasmus                           5          5           5               5   
Far Rockaway                      5          5           5               5   
Mariner's Harbor                  5          5           5               5   
Graniteville                      5          5           5               5   
Brownsville                       5          5           5               5   
Highland Park                     5          5           5               5   
Woodrow                           5          5           5               5   
Unionport                         5          5           5               5   
Sunset Park                       5          5           5               5   
Borough Park                      4          4           4               4   
West Farms                        4          4           4               4   
Crown Heights                     4          4           4               4   
Ditmas Park                       4          4           4               4   
Beechhurst                        4          4           4               4   
Port Richmond                     4          4           4               4   
Pleasant Plains                   4          4           4               4   
Bayswater                         4          4           4               4   
Parkchester                       4          4           4               4   
East Williamsburg                 4          4           4               4   
Weeksville                        4          4           4               4   
Egbertville                       4          4           4               4   
Elm Park                          4          4           4               4   
Oakwood                           4          4           4               4   
Prospect Heights                  4          4           4               4   
Emerson Hill                      4          4           4               4   
Westchester Square                4          4           4               4   
Westerleigh                       4          4           4               4   
Flatlands                         4          4           4               4   
Morris Park                       4          4           4               4   
Fort Greene                       4          4   

In [16]:

print('There are {} uniques categories.'.format(len(venues_df['Venue_Category'].unique())))

There are 350 uniques categories.


In [17]:
venues_df['Venue_Category'].unique()[:50]

array(['Dessert Shop', 'Caribbean Restaurant', 'Bakery', 'Pub', 'Bar',
       'Pizza Place', 'Pharmacy', 'Trail', 'Café', 'Grocery Store', 'Gym',
       'Bagel Shop', 'Brewery', 'Fast Food Restaurant', 'Ice Cream Shop',
       'Kitchen Supply Store', 'Seafood Restaurant', 'Wine Shop', 'Diner',
       'Brazilian Restaurant', 'Italian Restaurant', 'Pet Store',
       'Furniture / Home Store', 'American Restaurant',
       'Asian Restaurant', 'Sports Bar', 'Burger Joint', 'Park',
       'Donut Shop', 'Deli / Bodega', 'Mexican Restaurant', 'Coffee Shop',
       'Electronics Store', 'Botanical Garden',
       'Cajun / Creole Restaurant', 'Supermarket', 'Spanish Restaurant',
       'Japanese Restaurant', 'Garden', 'Track', 'Frozen Yogurt Shop',
       'Video Game Store', 'Liquor Store', 'Beer Bar', 'Exhibit',
       'Vineyard', 'Gift Shop', 'Breakfast Spot', 'Stables',
       'Cosmetics Shop'], dtype=object)

In [18]:

# one hot encoding
nyc_onehot = pd.get_dummies(venues_df[['Venue_Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nyc_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [nyc_onehot.columns[-1]] + list(nyc_onehot.columns[:-1])
nyc_onehot = nyc_onehot[fixed_columns]

print(nyc_onehot.shape)
nyc_onehot.head(10)

(30526, 351)


Neighborhoods  Accessories Store  African Restaurant  Airport Food Court  \
0     Wakefield                  0                   0                   0   
1     Wakefield                  0                   0                   0   
2     Wakefield                  0                   0                   0   
3     Wakefield                  0                   0                   0   
4     Wakefield                  0                   0                   0   
5     Wakefield                  0                   0                   0   
6     Wakefield                  0                   0                   0   
7     Wakefield                  0                   0                   0   
8     Wakefield                  0                   0                   0   
9     Wakefield                  0                   0                   0   

   Airport Lounge  Airport Service  American Restaurant  Amphitheater  \
0               0                0                    0             0   
1               0                0                    0             0   
2               0                0                    0             0   
3               0                0                    0             0   
4               0                0                    0             0   
5               0                0                    0             0   
6               0                0                    0             0   
7               0                0                    0             0   
8               0                0                    0             0   
9               0                0                    0             0   

   Animal Shelter  Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0               0         0       0                 0                       0   
1               0         0       0                 0                       0   
2               0         0       0                 0                       0   
3               0         0       0                 0                       0   
4               0         0       0                 0                       0   
5               0         0       0                 0                       0   
6               0         0       0                 0                       0   
7               0         0       0                 0                       0   
8               0         0       0                 0                       0   
9               0         0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   
5            0           0                    0                 0   
6            0           0                    0                 0   
7            0           0                    0                 0   
8            0           0                    0                 0   
9            0           0                    0                 0   

   Athletics & Sports  Austrian Restaurant  Automotive Shop  BBQ Joint  \
0                   0                    0                0          0   
1                   0                    0                0          0   
2                   0                    0                0          0   
3                   0                    0                0          0   
4                   0                    0                0          0   
5                   0                    0                0          0   
6                   0                    0                0          0   
7                   0                    0                0          0   
8                   0

In [19]:
nyc_grouped = nyc_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(nyc_grouped.shape)
nyc_grouped

(306, 351)


Neighborhoods  Accessories Store  African Restaurant  \
0                     Allerton           0.000000                0.00   
1                     Annadale           0.000000                0.00   
2                Arden Heights           0.000000                0.00   
3                    Arlington           0.010000                0.00   
4                     Arrochar           0.000000                0.00   
5                      Arverne           0.000000                0.00   
6                      Astoria           0.000000                0.00   
7              Astoria Heights           0.000000                0.00   
8                   Auburndale           0.000000                0.00   
9                   Bath Beach           0.000000                0.00   
10           Battery Park City           0.000000                0.00   
11                   Bay Ridge           0.000000                0.00   
12                  Baychester           0.000000                0.00   
13                     Bayside           0.000000                0.00   
14                   Bayswater           0.000000                0.00   
15                Bedford Park           0.000000                0.00   
16          Bedford Stuyvesant           0.000000                0.00   
17                  Beechhurst           0.000000                0.00   
18                    Bellaire           0.000000                0.00   
19                Belle Harbor           0.000000                0.00   
20                   Bellerose           0.000000                0.00   
21                     Belmont           0.000000                0.00   
22                 Bensonhurst           0.000000                0.00   
23                Bergen Beach           0.000000                0.00   
24                  Blissville           0.000000                0.00   
25                  Bloomfield           0.000000                0.00   
26                 Boerum Hill           0.000000                0.00   
27                Borough Park           0.000000                0.00   
28                Breezy Point           0.000000                0.00   
29                   Briarwood           0.000000                0.00   
30              Brighton Beach           0.000000                0.00   
31               Broad Channel           0.010309                0.00   
32           Broadway Junction           0.000000                0.00   
33                   Bronxdale           0.000000                0.00   
34            Brooklyn Heights           0.000000                0.00   
35                  Brookville           0.000000                0.00   
36                 Brownsville           0.000000                0.01   
37                  Bulls Head           0.000000                0.00   
38                    Bushwick           0.000000                0.00   
39                Butler Manor           0.000000                0.00   
40             Cambria Heights           0.000000                0.00   
41                    Canarsie           0.000000                0.00   
42               Carnegie Hill           0.000000                0.00   
43             Carroll Gardens           0.000000                0.00   
44                 Castle Hill           0.000000                0.00   
45           Castleton Corners           0.000000                0.00   
46              Central Harlem           0.000000                0.00   
47                  Charleston           0.000000                0.00   
48                   Chinatown           0.000000                0.00   
49                 City Island           0.000000                0.00   
50                   City Line           0.000000                0.00   
51                Civic Center           0.000000                0.00   
52           Claremont Village           0.000000                0.01   
53                Clason Point           0.000000                0.00   
54

In [20]:

len(nyc_grouped[nyc_grouped["Coffee Shop"] > 0])

275

In [21]:
nyc_coffeeshop = nyc_grouped[["Neighborhoods","Coffee Shop"]]
nyc_coffeeshop.head()

Neighborhoods  Coffee Shop
0       Allerton     0.030000
1       Annadale     0.010309
2  Arden Heights     0.010000
3      Arlington     0.030000
4       Arrochar     0.020000

In [22]:
nyc_coffeeshop=nyc_coffeeshop.sort_values(ascending=False,by='Coffee Shop')
nyc_coffeeshop.head()

Neighborhoods  Coffee Shop
111            Gowanus         0.06
216       Prince's Bay         0.06
53        Clason Point         0.06
171            Melrose         0.06
62   Concourse Village         0.06

### Cluster Neighborhoods
Run k-means to cluster the neighborhoods in NYC into 3 clusters.

In [23]:

# set number of clusters
kclusters = 3

nyc_clustering = nyc_coffeeshop.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:30]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [24]:
# Create a new dataframe that includes the cluster label
nyc_merged = nyc_coffeeshop.copy()

# add clustering labels
nyc_merged["Cluster Labels"] = kmeans.labels_


nyc_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
nyc_merged.head(10)

Neighborhood  Coffee Shop  Cluster Labels
111            Gowanus         0.06               1
216       Prince's Bay         0.06               1
53        Clason Point         0.06               1
171            Melrose         0.06               1
62   Concourse Village         0.06               1
65        Country Club         0.06               1
190           New Lots         0.06               1
38            Bushwick         0.06               1
199         Ocean Hill         0.06               1
201           Old Town         0.06               1

In [27]:
# nyc_merged = nyc_merged.join(neighborhoods.set_index("Neighborhood"), on="Neighborhood")

print(nyc_merged.shape)
dd=nyc_merged['Neighborhood']

new=nyc_merged[dd.isin(dd[dd.duplicated()])]
new=new
# nyc_merged[nyc_merged.duplicated(['Neighborhood'])] # check the last columns!

(306, 6)


In [28]:

# Sort the results by Cluster Labels
print(nyc_merged.shape)
nyc_merged.sort_values(["Cluster Labels"], inplace=True)
nyc_merged

(306, 6)


Neighborhood  Coffee Shop  Cluster Labels        Borough  \
50                   City Line     0.020000               0       Brooklyn   
98                    Flushing     0.020000               0         Queens   
241                   Rosedale     0.020000               0         Queens   
82                    Edenwald     0.020000               0          Bronx   
72                       Dumbo     0.020000               0       Brooklyn   
247                   Sea Gate     0.020000               0       Brooklyn   
242                  Rossville     0.020000               0  Staten Island   
167                Marble Hill     0.020000               0      Manhattan   
168                Marine Park     0.020000               0       Brooklyn   
286               Vinegar Hill     0.020000               0       Brooklyn   
109                  Glen Oaks     0.020000               0         Queens   
78                East Tremont     0.020000               0          Bronx   
146        Kingsbridge Heights     0.020000               0          Bronx   
144          Kew Gardens Hills     0.020000               0         Queens   
115                   Grasmere     0.020000               0  Staten Island   
118                 Greenpoint     0.020000               0       Brooklyn   
119                 Greenridge     0.020000               0  Staten Island   
107                 Georgetown     0.020000               0       Brooklyn   
105              Fresh Meadows     0.020000               0         Queens   
124          Heartland Village     0.020000               0  Staten Island   
101       Forest Hills Gardens     0.020000               0         Queens   
265      Staten Island_Chelsea     0.020000               0  Staten Island   
145                Kingsbridge     0.020000               0          Bronx   
99                     Fordham     0.020000               0          Bronx   
132               Howland Hook     0.020000               0  Staten Island   
275                Tottenville     0.020000               0  Staten Island   
276                     Travis     0.020000               0  Staten Island   
259             Spuyten Duyvil     0.020000               0          Bronx   
257                 South Side     0.020000               0       Brooklyn   
92                   Fieldston     0.020000               0          Bronx   
177                 Mill Basin     0.020000               0       Brooklyn   
170                    Maspeth     0.020000               0         Queens   
49                 City Island     0.030000               0          Bronx   
290              West Brighton     0.030000               0  Staten Island   
15                Bedford Park     0.030000               0          Bronx   
220             Queens Village     0.020000               0         Queens   
200              Ocean Parkway     0.020000               0       Brooklyn   
195                 North Side     0.020000               0       Brooklyn   
35                  Brookville     0.020000               0         Queens   
178                Mill Island     0.020000               0       Brooklyn   
203                 Ozone Park     0.020000               0         Queens   
204            Paerdegat Basin     0.020000               0       Brooklyn   
23                Bergen Beach     0.020000               0       Brooklyn   
20                   Bellerose     0.020000               0         Queens   
19                Belle Harbor     0.020000               0         Queens   
13                     Bayside     0.020000               0         Queens   
213                 Port Ivory     0.020000               0  Staten Island   
214                Port Morris     0.020000               0          Bronx   
142                 Kensington     0.020000               0       Brooklyn   
302                   Woodlawn     0.020000               0          Bronx   
221         Queens_Bay Terrace     0.020

In [29]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyc_merged['Latitude'], nyc_merged['Longitude'], nyc_merged['Neighborhood'], nyc_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [30]:
map_clusters.save('NYC_neighborhood_map_clusters.html')

### Examine Clusters

In [31]:
k_0=nyc_merged.loc[nyc_merged['Cluster Labels'] == 0].reset_index()
k_0

index           Neighborhood  Coffee Shop  Cluster Labels        Borough  \
0       50              City Line     0.020000               0       Brooklyn   
1       98               Flushing     0.020000               0         Queens   
2      241               Rosedale     0.020000               0         Queens   
3       82               Edenwald     0.020000               0          Bronx   
4       72                  Dumbo     0.020000               0       Brooklyn   
5      247               Sea Gate     0.020000               0       Brooklyn   
6      242              Rossville     0.020000               0  Staten Island   
7      167            Marble Hill     0.020000               0      Manhattan   
8      168            Marine Park     0.020000               0       Brooklyn   
9      286           Vinegar Hill     0.020000               0       Brooklyn   
10     109              Glen Oaks     0.020000               0         Queens   
11      78           East Tremont     0.020000               0          Bronx   
12     146    Kingsbridge Heights     0.020000               0          Bronx   
13     144      Kew Gardens Hills     0.020000               0         Queens   
14     115               Grasmere     0.020000               0  Staten Island   
15     118             Greenpoint     0.020000               0       Brooklyn   
16     119             Greenridge     0.020000               0  Staten Island   
17     107             Georgetown     0.020000               0       Brooklyn   
18     105          Fresh Meadows     0.020000               0         Queens   
19     124      Heartland Village     0.020000               0  Staten Island   
20     101   Forest Hills Gardens     0.020000               0         Queens   
21     265  Staten Island_Chelsea     0.020000               0  Staten Island   
22     145            Kingsbridge     0.020000               0          Bronx   
23      99                Fordham     0.020000               0          Bronx   
24     132           Howland Hook     0.020000               0  Staten Island   
25     275            Tottenville     0.020000               0  Staten Island   
26     276                 Travis     0.020000               0  Staten Island   
27     259         Spuyten Duyvil     0.020000               0          Bronx   
28     257             South Side     0.020000               0       Brooklyn   
29      92              Fieldston     0.020000               0          Bronx   
30     177             Mill Basin     0.020000               0       Brooklyn   
31     170                Maspeth     0.020000               0         Queens   
32      49            City Island     0.030000               0          Bronx   
33     290          West Brighton     0.030000               0  Staten Island   
34      15           Bedford Park     0.030000               0          Bronx   
35     220         Queens Village     0.020000               0         Queens   
36     200          Ocean Parkway     0.020000               0       Brooklyn   
37     195             North Side     0.020000               0       Brooklyn   
38      35             Brookville     0.020000               0         Queens   
39     178            Mill Island     0.020000               0       Brooklyn   
40     203             Ozone Park     0.020000               0         Queens   
41     204        Paerdegat Basin     0.020000               0       Brooklyn   
42      23           Bergen Beach     0.020000               0       Brooklyn   
43      20              Bellerose     0.020000               0         Queens   
44      19           Belle Harbor     0.020000               0         Queens   
45      13                Bayside     0.020000               0         Queens   
46     213             Port Ivory     0.020000               0  Staten Island   
47     214            Port Morris     0.020000               0          Bronx   
48     142             Kensington   

In [32]:
k_1=nyc_merged.loc[nyc_merged['Cluster Labels'] == 1]
k_1

Neighborhood  Coffee Shop  Cluster Labels        Borough  \
298                Willowbrook         0.04               1  Staten Island   
45           Castleton Corners         0.04               1  Staten Island   
289                 Weeksville         0.04               1       Brooklyn   
159                      Malba         0.04               1         Queens   
215              Port Richmond         0.04               1  Staten Island   
207                Parkchester         0.04               1          Bronx   
219        Prospect Park South         0.04               1       Brooklyn   
24                  Blissville         0.04               1         Queens   
299            Windsor Terrace         0.04               1       Brooklyn   
198                    Oakwood         0.04               1  Staten Island   
32           Broadway Junction         0.04               1       Brooklyn   
17                  Beechhurst         0.04               1         Queens   
294                Westerleigh         0.04               1  Staten Island   
27                Borough Park         0.04               1       Brooklyn   
217           Prospect Heights         0.04               1       Brooklyn   
136                Hunts Point         0.04               1          Bronx   
14                   Bayswater         0.04               1         Queens   
291                 West Farms         0.04               1          Bronx   
102                Fort Greene         0.04               1       Brooklyn   
211            Pleasant Plains         0.04               1  Staten Island   
77               East New York         0.05               1       Brooklyn   
86                    Elm Park         0.04               1  Staten Island   
240                   Rosebank         0.04               1  Staten Island   
58                 Cobble Hill         0.04               1       Brooklyn   
80           East Williamsburg         0.04               1       Brooklyn   
150            Lighthouse Hill         0.04               1  Staten Island   
85                 Egbertville         0.04               1  Staten Island   
266    Staten Island_Sunnyside         0.04               1  Staten Island   
261                 St. George         0.04               1  Staten Island   
253                  Soundview         0.04               1          Bronx   
75               East Flatbush         0.04               1       Brooklyn   
89                Emerson Hill         0.04               1  Staten Island   
96                   Flatlands         0.04               1       Brooklyn   
262                  Stapleton         0.04               1  Staten Island   
264  Staten Island_Bay Terrace         0.04               1  Staten Island   
274              Tompkinsville         0.04               1  Staten Island   
293         Westchester Square         0.04               1          Bronx   
232              Richmond Town         0.04               1  Staten Island   
154                Little Neck         0.04               1         Queens   
270                Sunset Park         0.05               1       Brooklyn   
36                 Brownsville         0.05               1       Brooklyn   
61                   Concourse         0.04               1          Bronx   
117                Great Kills         0.04               1  Staten Island   
244                      Rugby         0.04               1       Brooklyn   
68                 Ditmas Park         0.04               1       Brooklyn   
125               High  Bridge         0.04               1          Bronx   
303                    Woodrow         0.05               1  Staten Island   
44                 Castle Hill         0.05               1          Bronx   
245               Sandy Ground         0.04               1  Staten Island   
169           Mariner's Harbor         0.05               1  Staten Island   
91                Far Rockaway         0

In [33]:
k_2=nyc_merged.loc[nyc_merged['Cluster Labels'] == 2]
k_2

Neighborhood  Coffee Shop  Cluster Labels        Borough  \
277                Tribeca     0.010000               2      Manhattan   
1                 Annadale     0.010309               2  Staten Island   
304               Woodside     0.010000               2         Queens   
74           East Elmhurst     0.000000               2         Queens   
287              Wakefield     0.010000               2          Bronx   
231          Richmond Hill     0.010000               2         Queens   
269      Sunnyside Gardens     0.010000               2         Queens   
243                Roxbury     0.015152               2         Queens   
251                   Soho     0.010000               2      Manhattan   
229              Rego Park     0.010000               2         Queens   
64                  Corona     0.010000               2         Queens   
236               Rochdale     0.010000               2         Queens   
282        Upper East Side     0.010000               2      Manhattan   
296         Williamsbridge     0.010000               2          Bronx   
284                 Utopia     0.010000               2         Queens   
258    Springfield Gardens     0.010000               2         Queens   
248         Sheepshead Bay     0.010000               2       Brooklyn   
153           Little Italy     0.010000               2      Manhattan   
268        Stuyvesant Town     0.010000               2      Manhattan   
227             Ravenswood     0.010000               2         Queens   
260             St. Albans     0.010000               2         Queens   
131           Howard Beach     0.010000               2         Queens   
87                Elmhurst     0.010000               2         Queens   
128                 Hollis     0.010000               2         Queens   
127              Hillcrest     0.010000               2         Queens   
108        Gerritsen Beach     0.010000               2       Brooklyn   
106           Fulton Ferry     0.010000               2       Brooklyn   
100           Forest Hills     0.010000               2         Queens   
93      Financial District     0.010000               2      Manhattan   
6                  Astoria     0.010000               2         Queens   
81             Eastchester     0.010000               2          Bronx   
79            East Village     0.010000               2      Manhattan   
76             East Harlem     0.010000               2      Manhattan   
59           College Point     0.010000               2         Queens   
139         Jamaica Center     0.010000               2         Queens   
51            Civic Center     0.010000               2      Manhattan   
48               Chinatown     0.010000               2      Manhattan   
41                Canarsie     0.010000               2       Brooklyn   
30          Brighton Beach     0.010000               2       Brooklyn   
29               Briarwood     0.010000               2         Queens   
28            Breezy Point     0.010000               2         Queens   
25              Bloomfield     0.010000               2  Staten Island   
22             Bensonhurst     0.010000               2       Brooklyn   
18                Bellaire     0.010000               2         Queens   
10       Battery Park City     0.010000               2      Manhattan   
129             Holliswood     0.010000               2         Queens   
283        Upper West Side     0.010000               2      Manhattan   
278             Tudor City     0.000000               2      Manhattan   
192                   Noho     0.000000               2      Manhattan   
239       Roosevelt Island     0.000000               2      Manhattan   
162       Manhattan Valley     0.010000               2      Manhattan   
161      Manhattan Terrace     0.010000               2       Brooklyn   
160        Manhattan Beach     0.010000               2       Brooklyn   
157        Lower E

In [34]:
len_cluster_0 = len(k_0)
len_cluster_1 = len(k_1)
len_cluster_2 = len(k_2)

print('Total neighborhoods in cluster 0 =', len_cluster_0)
print('Total neighborhoods in cluster 1 =', len_cluster_1)
print('Total neighborhoods in cluster 2 =', len_cluster_2)

Total neighborhoods in cluster 0 = 132
Total neighborhoods in cluster 1 = 78
Total neighborhoods in cluster 2 = 96


# Conclusion

#### Cluster 0: means that the neighborhoods that have 2 or 3 Coffee Shops , around 43%


#### Cluster 1: means that the neighborhoods that have 4 or 5 or 6 Coffee Shops , around 25%


#### Cluster 2: means that the neighborhoods that have 1 Coffee Shop , around 31%

This is showing that new Coffee Shops can be opened in neighborhoods listed in cluster 1 as less competition compared to cluster 0 and 2. Meanwhile, Coffee Shops in cluster 1 are likely suffering from intense competition due to oversupply because cluster 1 is the neighborhoods that have 4,5 or 6 coffee shops. So we can figure out which boroughs have more coffee shops.

### Now we group them by neighborhood to understand which neighborhoods have more coffee shops

In [35]:
print(k_0.groupby(k_0['Borough']).count()['Coffee Shop'])
print(k_1.groupby(k_1['Borough']).count()['Coffee Shop'])
print(k_2.groupby(k_2['Borough']).count()['Coffee Shop'])



Borough
Bronx            29
Brooklyn         27
Manhattan         7
Queens           33
Staten Island    36
Name: Coffee Shop, dtype: int64
Borough
Bronx            16
Brooklyn         30
Manhattan         1
Queens            7
Staten Island    24
Name: Coffee Shop, dtype: int64
Borough
Bronx             7
Brooklyn         13
Manhattan        32
Queens           41
Staten Island     3
Name: Coffee Shop, dtype: int64


So, we concentrate on cluster 1. we know that the Queens, Brooklyn and Manhattan are crowded and their density of population are high. So, we can choose these 2 boroughs but as you can see from above, Brooklyn has many coffee shops on 30 neighborhoods. So, we rather to choose Manhattan and Queens because Manhattan has 6 coffee shops on just 1 neighborhood(Hamilton Heights) and Queens on 7 neighborhoods. The other neighborhoods are on cluster 0 or 2.Thus, we choose other neighborhoods except those neighborhoods.

In [38]:
print(k_1[(k_1['Borough'].isin(['Manhattan','Queens']))])
# print(k_1[k_1['Borough']=='Brooklyn'])


         Neighborhood  Coffee Shop  Cluster Labels    Borough   Latitude  \
159             Malba         0.04               1     Queens  40.790602   
24         Blissville         0.04               1     Queens  40.737251   
17         Beechhurst         0.04               1     Queens  40.792781   
14          Bayswater         0.04               1     Queens  40.611322   
154       Little Neck         0.04               1     Queens  40.770826   
91       Far Rockaway         0.05               1     Queens  40.603134   
172    Middle Village         0.04               1     Queens  40.716415   
122  Hamilton Heights         0.06               1  Manhattan  40.823604   

     Longitude  
159 -73.826678  
24  -73.932442  
17  -73.804365  
14  -73.765968  
154 -73.738898  
91  -73.754980  
172 -73.881143  
122 -73.949688  


### Eliminate 'Hamilton Heights','Middle Village','Beechhurst','Bayswater','Blissville','Little Neck','Malba','Far Rockaway'

In [39]:
manh_and_qu_data = neighborhoods[neighborhoods['Borough'].isin(['Manhattan','Queens'])].reset_index(drop=True)
manh_and_qu_boroughs=manh_and_qu_data[~(manh_and_qu_data['Neighborhood'].isin(['Hamilton Heights','Middle Village','Beechhurst','Bayswater','Blissville','Little Neck','Malba','Far Rockaway']))]
manh_and_qu_boroughs['Neighborhood']

0                Marble Hill
1                  Chinatown
2         Washington Heights
3                     Inwood
5             Manhattanville
6             Central Harlem
7                East Harlem
8            Upper East Side
9                  Yorkville
10                Lenox Hill
11          Roosevelt Island
12           Upper West Side
13            Lincoln Square
14                   Clinton
15                   Midtown
16     Manhattan_Murray Hill
17         Manhattan_Chelsea
18         Greenwich Village
19              East Village
20           Lower East Side
21                   Tribeca
22              Little Italy
23                      Soho
24              West Village
25          Manhattan Valley
26       Morningside Heights
27                  Gramercy
28         Battery Park City
29        Financial District
30                   Astoria
31                  Woodside
32           Jackson Heights
33                  Elmhurst
34              Howard Beach
35            

In [44]:
# manh_and_qu_boroughs
places_for_coffee_shops=manh_and_qu_boroughs[['Borough','Neighborhood']]
# copy=copy.reset_index()
# copy['Neighborhood']
final_result = places_for_coffee_shops.join(copy.set_index("Neighborhood"), on="Neighborhood")
final_result=final_result[['Borough','Neighborhood','Venue_Category']]
final_result=final_result[final_result['Venue_Category']>=0]
final_result=final_result.rename(columns={'Venue_Category':'Number Of Coffee Shops'})
final_result=final_result.reset_index()
final_result=final_result[['Borough','Neighborhood','Number Of Coffee Shops']]
final_result

Borough          Neighborhood  Number Of Coffee Shops
0   Manhattan           Marble Hill                     2.0
1   Manhattan             Chinatown                     1.0
2   Manhattan    Washington Heights                     3.0
3   Manhattan                Inwood                     3.0
4   Manhattan        Manhattanville                     3.0
5   Manhattan        Central Harlem                     3.0
6   Manhattan           East Harlem                     1.0
7   Manhattan       Upper East Side                     1.0
8   Manhattan             Yorkville                     1.0
9   Manhattan            Lenox Hill                     1.0
10  Manhattan       Upper West Side                     1.0
11  Manhattan          East Village                     1.0
12  Manhattan       Lower East Side                     1.0
13  Manhattan               Tribeca                     1.0
14  Manhattan          Little Italy                     1.0
15  Manhattan                  Soho                     1.0
16  Manhattan      Manhattan Valley                     1.0
17  Manhattan   Morningside Heights                     3.0
18  Manhattan     Battery Park City                     1.0
19  Manhattan    Financial District                     1.0
20     Queens               Astoria                     1.0
21     Queens              Woodside                     1.0
22     Queens              Elmhurst                     1.0
23     Queens          Howard Beach                     1.0
24     Queens                Corona                     1.0
25     Queens          Forest Hills                     1.0
26     Queens           Kew Gardens                     1.0
27     Queens         Richmond Hill                     1.0
28     Queens              Flushing                     2.0
29     Queens      Long Island City                     1.0
30     Queens      Queens_Sunnyside                     3.0
31     Queens               Maspeth                     2.0
32     Queens             Ridgewood                     3.0
33     Queens              Glendale                     2.0
34     Queens             Rego Park                     1.0
35     Queens            Ozone Park                     2.0
36     Queens      South Ozone Park                     3.0
37     Queens         College Point                     1.0
38     Queens            Whitestone                     3.0
39     Queens               Bayside                     2.0
40     Queens            Auburndale                     3.0
41     Queens            Douglaston                     3.0
42     Queens             Glen Oaks                     2.0
43     Queens             Bellerose                     2.0
44     Queens     Kew Gardens Hills                     2.0
45     Queens         Fresh Meadows                     2.0
46     Queens             Briarwood                     1.0
47     Queens        Jamaica Center                     1.0
48     Queens       Oakland Gardens                     1.0
49     Queens        Queens Village                     2.0
50     Queens                Hollis                     1.0
51     Queens         South Jamaica                     2.0
52     Queens            St. Albans                     1.0
53     Queens              Rochdale                     1.0
54     Queens   Springfield Gardens                     1.0
55     Queens              Rosedale                     2.0
56     Queens         Broad Channel                     3.0
57     Queens          Breezy Point                     1.0
58     Queens    Queens_Bay Terrace                     2.0
59     Queens              Edgemere                     3.0
60     Queens               Arverne                     3.0
61     Queens        Rockaway Beach                     3.0
62     Queens              Neponsit                     2.0
63     Queens    Queens_Murray Hill                     2.0
64     Queens           Floral Park                     3.0
65     Queens            Holliswood           